In [1]:
import pandas as pd
import numpy as np
#import kaleido
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import holidays
from datetime import date
from dateutil.relativedelta import relativedelta 
# This code below is to import an excel or csv for python to plot
import os

# Label Peaks

In [2]:
def clean_data(df, date_name, melt_vector = [], row  = True):
    if row:
        df = df.melt(id_vars= melt_vector, var_name='Time') 

    # Combine     
    df[date_name] = pd.to_datetime(df.Date.astype(str)+' '+df.Time.astype(str))
    # Delete time column since it is not needed
    df = df.drop(columns=['Time'])
    # Now python will sort the dataframe by time AND date
    df = df.sort_values([date_name])
    # This will renumber the resorted values from 0 to len(df)
    df = df.reset_index(drop=True)
    # This will rename the column  
    df = df.rename(columns={'value': 'Demand'})
    # This will convert everything to numeric
    df.Demand = pd.to_numeric(df.Demand, errors='coerce')
    
    return df

In [3]:
 # -*- coding: utf-8 -*-

#  python-holidays
#  ---------------
#  A fast, efficient Python library for generating country, province and state
#  specific sets of holidays on the fly. It aims to make determining whether a
#  specific date is a holiday as fast and flexible as possible.
#
#  Author:  ryanss <ryanssdev@icloud.com> (c) 2014-2017
#           dr-prodigy <maurizio.montel@gmail.com> (c) 2017-2020
#  Website: https://github.com/dr-prodigy/python-holidays
#  License: MIT (see LICENSE file)

from datetime import date, datetime, timedelta
from dateutil.easter import easter, EASTER_ORTHODOX
from dateutil.parser import parse
from dateutil.relativedelta import relativedelta as rd
from dateutil.relativedelta import MO, TU, WE, TH, FR, SA, SU
import inspect
import six
import sys
import warnings

__version__ = '0.9.12'

MON, TUE, WED, THU, FRI, SAT, SUN = range(7)
WEEKEND = (SAT, SUN)

JAN, FEB, MAR, APR, MAY, JUN, JUL, AUG, SEP, OCT, \
    NOV, DEC = range(1, 13)


class HolidayBase(dict):
    PROVINCES = []

    def __init__(self, years=[], expand=True, observed=True,
                 prov=None, state=None):
        self.observed = observed
        self.expand = expand
        if isinstance(years, int):
            years = [years, ]
        self.years = set(years)
        if not getattr(self, 'prov', False):
            self.prov = prov
        self.state = state
        for year in list(self.years):
            self._populate(year)

    def __setattr__(self, key, value):
        if key == 'observed' and len(self) > 0:
            dict.__setattr__(self, key, value)
            if value is True:
                # Add (Observed) dates
                years = list(self.years)
                self.years = set()
                self.clear()
                for year in years:
                    self._populate(year)
            else:
                # Remove (Observed) dates
                for k, v in list(self.items()):
                    if v.find("Observed") >= 0:
                        del self[k]
        else:
            return dict.__setattr__(self, key, value)

    def __keytransform__(self, key):
        if isinstance(key, datetime):
            key = key.date()
        elif isinstance(key, date):
            key = key
        elif isinstance(key, int) or isinstance(key, float):
            key = datetime.utcfromtimestamp(key).date()
        elif isinstance(key, six.string_types):
            try:
                key = parse(key).date()
            except (ValueError, OverflowError):
                raise ValueError("Cannot parse date from string '%s'" % key)
        else:
            raise TypeError("Cannot convert type '%s' to date." % type(key))

        if self.expand and key.year not in self.years:
            self.years.add(key.year)
            self._populate(key.year)
        return key

    def __contains__(self, key):
        return dict.__contains__(self, self.__keytransform__(key))

    def __getitem__(self, key):
        if isinstance(key, slice):
            if not key.start or not key.stop:
                raise ValueError("Both start and stop must be given.")

            start = self.__keytransform__(key.start)
            stop = self.__keytransform__(key.stop)

            if key.step is None:
                step = 1
            elif isinstance(key.step, timedelta):
                step = key.step.days
            elif isinstance(key.step, int):
                step = key.step
            else:
                raise TypeError(
                    "Cannot convert type '%s' to int." % type(key.step)
                )

            if step == 0:
                raise ValueError('Step value must not be zero.')

            date_diff = stop - start
            if date_diff.days < 0 <= step or date_diff.days >= 0 > step:
                step *= -1

            days_in_range = []
            for delta_days in range(0, date_diff.days, step):
                day = start + timedelta(days=delta_days)
                try:
                    dict.__getitem__(
                        self,
                        day
                    )
                    days_in_range.append(day)
                except (KeyError):
                    pass
            return days_in_range
        return dict.__getitem__(self, self.__keytransform__(key))

    def __setitem__(self, key, value):
        if key in self:
            if self.get(key).find(value) < 0 \
                    and value.find(self.get(key)) < 0:
                value = "%s, %s" % (value, self.get(key))
            else:
                value = self.get(key)
        return dict.__setitem__(self, self.__keytransform__(key), value)

    def update(self, *args):
        args = list(args)
        for arg in args:
            if isinstance(arg, dict):
                for key, value in list(arg.items()):
                    self[key] = value
            elif isinstance(arg, list):
                for item in arg:
                    self[item] = "Holiday"
            else:
                self[arg] = "Holiday"

    def append(self, *args):
        return self.update(*args)

    def get(self, key, default=None):
        return dict.get(self, self.__keytransform__(key), default)

    def get_list(self, key):
        return [h for h in self.get(key, "").split(", ") if h]

    def pop(self, key, default=None):
        if default is None:
            return dict.pop(self, self.__keytransform__(key))
        return dict.pop(self, self.__keytransform__(key), default)

    def __eq__(self, other):
        return dict.__eq__(self, other) and self.__dict__ == other.__dict__

    def __ne__(self, other):
        return dict.__ne__(self, other) or self.__dict__ != other.__dict__

    def __add__(self, other):
        if isinstance(other, int) and other == 0:
            # Required to sum() list of holidays
            # sum([h1, h2]) is equivalent to (0 + h1 + h2)
            return self
        elif not isinstance(other, HolidayBase):
            raise TypeError()
        HolidaySum = createHolidaySum(self, other)
        country = (getattr(self, 'country', None) or
                   getattr(other, 'country', None))
        if self.country and other.country and self.country != other.country:
            c1 = self.country
            if not isinstance(c1, list):
                c1 = [c1]
            c2 = other.country
            if not isinstance(c2, list):
                c2 = [c2]
            country = c1 + c2
        prov = getattr(self, 'prov', None) or getattr(other, 'prov', None)
        if self.prov and other.prov and self.prov != other.prov:
            p1 = self.prov if isinstance(self.prov, list) else [self.prov]
            p2 = other.prov if isinstance(other.prov, list) else [other.prov]
            prov = p1 + p2
        return HolidaySum(years=(self.years | other.years),
                          expand=(self.expand or other.expand),
                          observed=(self.observed or other.observed),
                          country=country, prov=prov)

    def __radd__(self, other):
        return self.__add__(other)

    def _populate(self, year):
        pass


def createHolidaySum(h1, h2):
    class HolidaySum(HolidayBase):

        def __init__(self, country, **kwargs):
            self.country = country
            self.holidays = []
            if getattr(h1, 'holidays', False):
                for h in h1.holidays:
                    self.holidays.append(h)
            else:
                self.holidays.append(h1)
            if getattr(h2, 'holidays', False):
                for h in h2.holidays:
                    self.holidays.append(h)
            else:
                self.holidays.append(h2)
            HolidayBase.__init__(self, **kwargs)

        def _populate(self, year):
            for h in self.holidays[::-1]:
                h._populate(year)
                self.update(h)

    return HolidaySum


def list_supported_countries():
    """List all supported countries incl. their abbreviation."""
    return [name for name, obj in
            inspect.getmembers(sys.modules[__name__], inspect.isclass)
            if obj.__module__ is __name__]


def CountryHoliday(country, years=[], prov=None, state=None, expand=True,
                   observed=True):
    try:
        country_holiday = globals()[country](years=years,
                                             prov=prov,
                                             state=state,
                                             expand=expand,
                                             observed=observed)
    except (KeyError):
        raise KeyError("Country %s not available" % country)
    return country_holiday

 class UsElectricHolidays(holidays.HolidayBase):
 
    def _populate(self, year):
         # New Year's Day
        if year > 1870:
            name = "New Year's Day"
            self[date(year, JAN, 1)] = name
            if self.observed and date(year, JAN, 1).weekday() == SUN:
                self[date(year, JAN, 1) + rd(days=+1)] = name + \
                    " (Observed)"

        # Washington's Birthday
        name = "Washington's Birthday"
        if year > 1970:
            self[date(year, FEB, 1) + rd(weekday=MO(+3))] = name
        elif year >= 1879:
            self[date(year, FEB, 22)] = name

        # Memorial Day
        if year > 1970:
            self[date(year, MAY, 31) + rd(weekday=MO(-1))] = "Memorial Day"
        elif year >= 1888:
            self[date(year, MAY, 30)] = "Memorial Day"

        # Independence Day
        if year > 1870:
            name = "Independence Day"
            self[date(year, JUL, 4)] = name
            if self.observed and date(year, JUL, 4).weekday() == SUN:
                self[date(year, JUL, 4) + rd(days=+1)] = name + " (Observed)"

        # Labor Day
        if year >= 1894:
            self[date(year, SEP, 1) + rd(weekday=MO)] = "Labor Day"

        # Veterans Day
        if year > 1953:
            name = "Veterans Day"
        else:
            name = "Armistice Day"
        if 1978 > year > 1970:
            self[date(year, OCT, 1) + rd(weekday=MO(+4))] = name
        elif year >= 1938:
            self[date(year, NOV, 11)] = name
            if self.observed \
                    and date(year, NOV, 11).weekday() == SUN:
                self[date(year, NOV, 11) + rd(days=+1)] = name + \
                    " (Observed)"

        # Thanksgiving
        if year > 1870:
            self[date(year, NOV, 1) + rd(weekday=TH(+4))] = "Thanksgiving"
            
        # Christmas Day
        if year > 1870:
            name = "Christmas Day"
            self[date(year, DEC, 25)] = "Christmas Day"
            if self.observed \
                    and date(year, DEC, 25).weekday() == SUN:
                self[date(year, DEC, 25) + rd(days=+1)] = name + \
                    " (Observed)"
        
us_holidays = UsElectricHolidays()

In [4]:
def label_weekends(df, timestamp_name):
    # Make the index the date
    df.index = df[timestamp_name]

    # Creates column for day of the week: 0 = Monday to 6 = Sunday
    df['DayWeek'] = df[timestamp_name].dt.dayofweek 
    # .apply run a function through every line of code without usong a for loop
    # lambda is a temporay function 
    # If x >= 5 set true (boolean statement) since it is the weekend # 5 is Saturday and 6 is Sunday
    # Returns boolean staement where weekend is true 
    df['Is_Weekend'] = df['DayWeek'].apply(lambda x: True if x >= 5 else False )
    # Creates an array for all the US Holidays in California
    # us_holidays = holidays.CountryHoliday('US')
    # Uses apply and lambda again to check if there is a holiday 
    # X in holiday returns a boolean satement 
    # .apply runs this function thorugh the entire Date column 
    # Returns a new boolean column where holidays is true 
    df['Is_Holiday'] = df[timestamp_name].apply(lambda x: True if x in us_holidays else False )
    # Creates a new column of Boolean satements of where summer is true
    # 6 is June and 9 is September
    df['is_summer'] = df[timestamp_name].dt.month.between(6,9)

    # This function determines the four catogories of Summer Weekend, Winter Weekend, Summer Weekday, Winter Weekday
    # The function takes in 4 columns in the dataframme
    # THhe .apply() function passes in one variable at a time from each column
    def peak_fun(vec):
        Date = vec[0] # First Column Date, .apply() Passes in a timestamp not a vector
        Is_Weekend = vec[1] # Second Column Is Weekend, .apply() Passes in a bool not a vector
        Is_Holiday = vec[2] # Third Column Is Holiday, .apply() Passes in a bool not a vector
        Is_Summer = vec[3] # Fourth Column Is Summer, .apply() Passes in a bool not a vector
        if Is_Weekend or Is_Holiday:
            if Is_Summer:
                return 'Summer_Weekend'       
            else:
                return 'Winter_Weekend'
        else:
            if Is_Summer:
                return 'Summer_Weekday'
            else:
                return 'Winter_Weekday'

    # Pass in the 4 columns and use the .apply() function
    df['fun'] = df[[timestamp_name, 'Is_Weekend', 'Is_Holiday', 'is_summer']].apply(peak_fun, axis = 1)
    return df 

In [6]:
# Declare Arrays
# Summer Weekday Time
su_wdy_sofpk = {} 
su_wdy_ofpk = {} 
su_wdy_mdpk = {}
su_wdy_onpk = {}

# Summer Weekend Time
su_wkd_sofpk = {}
su_wkd_ofpk = {}
su_wkd_mdpk = {}
su_wkd_onpk = {}

# Winter Weekday Time
wt_wdy_sofpk = {}
wt_wdy_ofpk = {}
wt_wdy_mdpk = {}
wt_wdy_onpk = {}

# Winter Weekend Time
wt_wkd_sofpk = {}
wt_wkd_ofpk = {}
wt_wkd_mdpk = {}
wt_wkd_onpk = {}

In [7]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[0] = False
su_wdy_ofpk[0] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[0] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[0] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[0] = False
su_wkd_ofpk[0] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[0] = False
su_wkd_onpk[0] = False

# Winter Weekday Time
wt_wdy_sofpk[0] = False
wt_wdy_ofpk[0] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[0] = ['8:00', '17:00']
wt_wdy_onpk[0] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[0] = False
wt_wkd_ofpk[0] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[0] = False
wt_wkd_onpk[0] = False

In [8]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[1] = False
su_wdy_ofpk[1] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[1] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[1] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[1] = False
su_wkd_ofpk[1] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[1] = False
su_wkd_onpk[1] = False

# Winter Weekday Time
wt_wdy_sofpk[1] = False
wt_wdy_ofpk[1] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[1] = ['8:00', '17:00']
wt_wdy_onpk[1] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[1] = False
wt_wkd_ofpk[1] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[1] = False
wt_wkd_onpk[1] = False

In [9]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[2] = False
su_wdy_ofpk[2] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[2] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[2] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[2] = False
su_wkd_ofpk[2] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[2] = False
su_wkd_onpk[2] = False

# Winter Weekday Time
wt_wdy_sofpk[2] = False
wt_wdy_ofpk[2] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[2] = ['8:00', '17:00']
wt_wdy_onpk[2] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[2] = False
wt_wkd_ofpk[2] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[2] = False
wt_wkd_onpk[2] = False

In [10]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[3] = False
su_wdy_ofpk[3] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[3] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[3] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[3] = False
su_wkd_ofpk[3] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[3] = False
su_wkd_onpk[3] = False

# Winter Weekday Time
wt_wdy_sofpk[3] = False
wt_wdy_ofpk[3] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[3] = ['8:00', '17:00']
wt_wdy_onpk[3] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[3] = False
wt_wkd_ofpk[3] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[3] = False
wt_wkd_onpk[3] = False

In [11]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[4] = False
su_wdy_ofpk[4] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[4] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[4] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[4] = False
su_wkd_ofpk[4] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[4] = False
su_wkd_onpk[4] = False

# Winter Weekday Time
wt_wdy_sofpk[4] = False
wt_wdy_ofpk[4] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[4] = ['8:00', '17:00']
wt_wdy_onpk[4] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[4] = False
wt_wkd_ofpk[4] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[4] = False
wt_wkd_onpk[4] = False

In [12]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[5] = False
su_wdy_ofpk[5] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[5] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[5] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[5] = False
su_wkd_ofpk[5] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[5] = False
su_wkd_onpk[5] = False

# Winter Weekday Time
wt_wdy_sofpk[5] = False
wt_wdy_ofpk[5] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[5] = ['8:00', '17:00']
wt_wdy_onpk[5] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[5] = False
wt_wkd_ofpk[5] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[5] = False
wt_wkd_onpk[5] = False

In [13]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[6] = False
su_wdy_ofpk[6] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[6] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[6] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[6] = False
su_wkd_ofpk[6] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[6] = False
su_wkd_onpk[6] = False

# Winter Weekday Time
wt_wdy_sofpk[6] = False
wt_wdy_ofpk[6] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[6] = ['8:00', '17:00']
wt_wdy_onpk[6] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[6] = False
wt_wkd_ofpk[6] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[6] = False
wt_wkd_onpk[6] = False

In [14]:
# RPU TOU Pricing 
# Summer Weekday Time
su_wdy_sofpk[7] = False
su_wdy_ofpk[7] = ['0:00','8:00','23:00','0:00']
su_wdy_mdpk[7] = ['8:00', '12:00', '18:00', '23:00']
su_wdy_onpk[7] = ['12:00', '18:00']

# Summer Weekend Time
su_wkd_sofpk[7] = False
su_wkd_ofpk[7] = ['0:00','21:00','21:00','0:00']
su_wkd_mdpk[7] = False
su_wkd_onpk[7] = False

# Winter Weekday Time
wt_wdy_sofpk[7] = False
wt_wdy_ofpk[7] = ['0:00','8:00','21:00','0:00']
wt_wdy_mdpk[7] = ['8:00', '17:00']
wt_wdy_onpk[7] = ['17:00', '21:00']

# Winter Weekend Time
wt_wkd_sofpk[7] = False
wt_wkd_ofpk[7] = ['0:00','21:00','21:00','0:00']
wt_wkd_mdpk[7] = False
wt_wkd_onpk[7] = False

In [15]:
def summer_weekday(su_wdy_sofpk, su_wdy_ofpk, su_wdy_mdpk, su_wdy_onpk, df):
    
    if su_wdy_sofpk != False:
        len_su_wdy_sofpk = int(len(su_wdy_sofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wdy_sofpk,1):
            selection = df[df['fun'] == 'Summer_Weekday'].between_time(su_wdy_sofpk[begin],su_wdy_sofpk[end], include_end=False)
            selection["Peak"] = "Super Off-Peak"
            ww = df["fun"] == "Summer_Weekday"
            df.loc[df[ww].between_time(su_wdy_sofpk[begin], su_wdy_sofpk[end], include_end=False).index, "Peak"] = "Super Off-Peak"
            begin += 2
            end += 2
            
    if su_wdy_ofpk != False:
        len_su_wdy_ofpk = int(len(su_wdy_ofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wdy_ofpk,1):
            selection = df[df['fun'] == 'Summer_Weekday'].between_time(su_wdy_ofpk[begin],su_wdy_ofpk[end], include_end=False)
            selection["Peak"] = "Off-Peak"
            ww = df["fun"] == "Summer_Weekday"
            df.loc[df[ww].between_time(su_wdy_ofpk[begin], su_wdy_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
            begin += 2
            end += 2
    
    if su_wdy_mdpk != False:
        len_su_wdy_mdpk = int(len(su_wdy_mdpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wdy_mdpk,1):
            selection = df[df['fun'] == 'Summer_Weekday'].between_time(su_wdy_mdpk[begin],su_wdy_mdpk[end], include_end=False)
            selection["Peak"] = "Mid-Peak"
            ww = df["fun"] == "Summer_Weekday"
            df.loc[df[ww].between_time(su_wdy_mdpk[begin], su_wdy_mdpk[end], include_end=False).index, "Peak"] = "Mid-Peak"
            begin += 2
            end += 2
    
    if su_wdy_onpk != False:
        len_su_wdy_onpk = int(len(su_wdy_onpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wdy_onpk,1):
            selection = df[df['fun'] == 'Summer_Weekday'].between_time(su_wdy_onpk[begin],su_wdy_onpk[end], include_end=False)
            selection["Peak"] = "On-Peak"
            ww = df["fun"] == "Summer_Weekday"
            df.loc[df[ww].between_time(su_wdy_onpk[begin], su_wdy_onpk[end], include_end=False).index, "Peak"] = "On-Peak"
            begin += 2
            end += 2
    return df

def summer_weekend(su_wkd_sofpk, su_wkd_ofpk, su_wkd_mdpk, su_wkd_onpk, df):
    
    if su_wkd_sofpk != False:
        len_su_wkd_sofpk = int(len(su_wkd_sofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wkd_sofpk,1):
            selection = df[df['fun'] == 'Summer_Weekend'].between_time(su_wkd_sofpk[begin],su_wkd_sofpk[end], include_end=False)
            selection["Peak"] = "Super Off-Peak"
            ww = df["fun"] == "Summer_Weekend"
            df.loc[df[ww].between_time(su_wkd_sofpk[begin], su_wkd_sofpk[end], include_end=False).index, "Peak"] = "Super Off-Peak"
            begin += 2
            end += 2
            
    if su_wkd_ofpk != False:
        len_su_wkd_ofpk = int(len(su_wkd_ofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wkd_ofpk,1):
            selection = df[df['fun'] == 'Summer_Weekend'].between_time(su_wkd_ofpk[begin],su_wkd_ofpk[end], include_end=False)
            selection["Peak"] = "Off-Peak"
            ww = df["fun"] == "Summer_Weekend"
            df.loc[df[ww].between_time(su_wkd_ofpk[begin], su_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
            begin += 2
            end += 2
    
    if su_wkd_mdpk != False:
        len_su_wkd_mdpk = int(len(su_wkd_mdpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wkd_mdpk,1):
            selection = df[df['fun'] == 'Summer_Weekend'].between_time(su_wkd_mdpk[begin],su_wkd_mdpk[end], include_end=False)
            selection["Peak"] = "Mid-Peak"
            ww = df["fun"] == "Summer_Weekend"
            df.loc[df[ww].between_time(su_wkd_mdpk[begin], su_wkd_mdpk[end], include_end=False).index, "Peak"] = "Mid-Peak"
            begin += 2
            end += 2
    
    if su_wkd_onpk != False:
        len_su_wkd_onpk = int(len(su_wkd_onpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_su_wkd_onpk,1):
            selection = df[df['fun'] == 'Summer_Weekend'].between_time(su_wkd_onpk[begin],su_wkd_onpk[end], include_end=False)
            selection["Peak"] = "On-Peak"
            ww = df["fun"] == "Summer_Weekend"
            df.loc[df[ww].between_time(su_wkd_onpk[begin], su_wkd_onpk[end], include_end=False).index, "Peak"] = "On-Peak"
            begin += 2
            end += 2
    return df

def winter_weekday(wt_wdy_sofpk, wt_wdy_ofpk, wt_wdy_mdpk, wt_wdy_onpk, df):
    
    if wt_wdy_sofpk != False:
        len_wt_wdy_sofpk = int(len(wt_wdy_sofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wdy_sofpk,1):
            selection = df[df['fun'] == 'Winter_Weekday'].between_time(wt_wdy_sofpk[begin],wt_wdy_sofpk[end], include_end=False)
            selection["Peak"] = "Super Off-Peak"
            ww = df["fun"] == "Winter_Weekday"
            df.loc[df[ww].between_time(wt_wdy_sofpk[begin], wt_wdy_sofpk[end], include_end=False).index, "Peak"] = "Super Off-Peak"
            begin += 2
            end += 2
            
    if wt_wdy_ofpk != False:
        len_wt_wdy_ofpk = int(len(wt_wdy_ofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wdy_ofpk,1):
            selection = df[df['fun'] == 'Winter_Weekday'].between_time(wt_wdy_ofpk[begin],wt_wdy_ofpk[end], include_end=False)
            selection["Peak"] = "Off-Peak"
            ww = df["fun"] == "Winter_Weekday"
            df.loc[df[ww].between_time(wt_wdy_ofpk[begin], wt_wdy_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
            begin += 2
            end += 2
    
    if wt_wdy_mdpk != False:
        len_wt_wdy_mdpk = int(len(wt_wdy_mdpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wdy_mdpk,1):
            selection = df[df['fun'] == 'Winter_Weekday'].between_time(wt_wdy_mdpk[begin],wt_wdy_mdpk[end], include_end=False)
            selection["Peak"] = "Mid-Peak"
            ww = df["fun"] == "Winter_Weekday"
            df.loc[df[ww].between_time(wt_wdy_mdpk[begin], wt_wdy_mdpk[end], include_end=False).index, "Peak"] = "Mid-Peak"
            begin += 2
            end += 2
    
    if wt_wdy_onpk != False:
        len_wt_wdy_onpk = int(len(wt_wdy_onpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wdy_onpk,1):
            selection = df[df['fun'] == 'Winter_Weekday'].between_time(wt_wdy_onpk[begin],wt_wdy_onpk[end], include_end=False)
            selection["Peak"] = "On-Peak"
            ww = df["fun"] == "Winter_Weekday"
            df.loc[df[ww].between_time(wt_wdy_onpk[begin], wt_wdy_onpk[end], include_end=False).index, "Peak"] = "On-Peak"
            begin += 2
            end += 2
    return df

def winter_weekend(wt_wkd_sofpk, wt_wkd_ofpk, wt_wkd_mdpk, wt_wkd_onpk, df):
    
    if wt_wkd_sofpk != False:
        len_wt_wkd_sofpk = int(len(wt_wkd_sofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wkd_sofpk,1):
            selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_sofpk[begin],wt_wkd_sofpk[end], include_end=False)
            selection["Peak"] = "Super Off-Peak"
            ww = df["fun"] == "Winter_Weekend"
            df.loc[df[ww].between_time(wt_wkd_sofpk[begin], wt_wkd_sofpk[end], include_end=False).index, "Peak"] = "Super Off-Peak"
            begin += 2
            end += 2
            
    if wt_wkd_ofpk != False:
        len_wt_wkd_ofpk = int(len(wt_wkd_ofpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wkd_ofpk,1):
            selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
            selection["Peak"] = "Off-Peak"
            ww = df["fun"] == "Winter_Weekend"
            df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
            begin += 2
            end += 2
    
    if wt_wkd_mdpk != False:
        len_wt_wkd_mdpk = int(len(wt_wkd_mdpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wkd_mdpk,1):
            selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_mdpk[begin],wt_wkd_mdpk[end], include_end=False)
            selection["Peak"] = "Mid-Peak"
            ww = df["fun"] == "Winter_Weekend"
            df.loc[df[ww].between_time(wt_wkd_mdpk[begin], wt_wkd_mdpk[end], include_end=False).index, "Peak"] = "Mid-Peak"
            begin += 2
            end += 2
    
    if wt_wkd_onpk != False:
        len_wt_wkd_onpk = int(len(wt_wkd_onpk)/2)
        begin = 0
        end = 1
        for i in range(0,len_wt_wkd_onpk,1):
            selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_onpk[begin],wt_wkd_onpk[end], include_end=False)
            selection["Peak"] = "On-Peak"
            ww = df["fun"] == "Winter_Weekend"
            df.loc[df[ww].between_time(wt_wkd_onpk[begin], wt_wkd_onpk[end], include_end=False).index, "Peak"] = "On-Peak"
            begin += 2
            end += 2
    return df

In [16]:
def label_peaks(df, i):
    winter_weekend(wt_wkd_sofpk[i], wt_wkd_ofpk[i], wt_wkd_mdpk[i], wt_wkd_onpk[i], df)
    winter_weekday(wt_wdy_sofpk[i], wt_wdy_ofpk[i], wt_wdy_mdpk[i], wt_wdy_onpk[i], df)
    summer_weekday(su_wdy_sofpk[i], su_wdy_ofpk[i], su_wdy_mdpk[i], su_wdy_onpk[i], df)
    summer_weekend(su_wkd_sofpk[i], su_wkd_ofpk[i], su_wkd_mdpk[i], su_wkd_onpk[i], df)

In [17]:
def resample(df, time_column = 'time', resample_rate = '15T'):
    df[time_column] = pd.to_datetime(df[time_column])
    df = df.set_index(df[time_column])
    df = df.drop(columns = [time_column])
    df = df.resample(resample_rate).mean()  #df.groupby(pd.Grouper(key=time_column, freq=resample_rate)).ffill().bfill() 
    df.insert(loc=0, column=time_column, value=df.index) #df.insert(loc=0, column=time_column, value=np.arange(0, len(df.index), 1, dtype=int)) #
    df = df.reset_index(drop=True)
    return df

In [18]:
os.chdir('/home/lencon/Git_Research/FISTS_2024/Code/Microgrid_Data/fists_simulations_data')
s1 = pd.read_csv('fists_paper_microgrid_no_bess_no_ev_run_0.csv')
s2 = pd.read_csv('fists_paper_microgrid_no_bess_l2_run_0.csv')
s3 = pd.read_csv('fists_paper_microgrid_no_bess_l3_run_0.csv')
s4 = pd.read_csv('fists_paper_microgrid_no_bess_l2_l3_run_0.csv')
s5 = pd.read_csv('fists_paper_microgrid_bess_no_ev_run_0.csv')
s6 = pd.read_csv('fists_paper_microgrid_bess_l2_run_0.csv')
s7 = pd.read_csv('fists_paper_microgrid_bess_l3_run_0.csv')
s8 = pd.read_csv('fists_paper_microgrid_bess_l2_l3_run_0.csv')
df = [s1, s2, s3, s4, s5, s6, s7, s8]
df

[                time  BESS.P  building_load.P  ev_charger_level_2_load.P  \
 0       0.000000e+00       0     -8383.000000                          0   
 1       0.000000e+00       0     -8383.000000                          0   
 2       0.000000e+00       0     -8383.000000                          0   
 3       8.999743e+02       0     -8896.985331                          0   
 4       9.000000e+02       0     -8897.000000                          0   
 ...              ...     ...              ...                        ...   
 175192  3.153420e+07       0     -7092.000392                          0   
 175193  3.153420e+07       0     -7092.003196                          0   
 175194  3.153510e+07       0     -7204.000000                          0   
 175195  3.153510e+07       0     -7204.000000                          0   
 175196  3.153510e+07       0     -7204.000000                          0   
 
         ev_charger_level_3_load.P  generator.P  grid.sou.S[1]  \
 0      

In [19]:
for i in range(len(df)):
    df[i]['time'] = pd.to_datetime(df[i]['time'] + 1646092800, unit = 's')
df

[                                time  BESS.P  building_load.P  \
 0      2022-03-01 00:00:00.000000000       0     -8383.000000   
 1      2022-03-01 00:00:00.000000000       0     -8383.000000   
 2      2022-03-01 00:00:00.000000000       0     -8383.000000   
 3      2022-03-01 00:14:59.974315264       0     -8896.985331   
 4      2022-03-01 00:15:00.000000000       0     -8897.000000   
 ...                              ...     ...              ...   
 175192 2023-02-28 23:30:00.003153664       0     -7092.000392   
 175193 2023-02-28 23:30:00.025684736       0     -7092.003196   
 175194 2023-02-28 23:45:00.000000000       0     -7204.000000   
 175195 2023-02-28 23:45:00.000000000       0     -7204.000000   
 175196 2023-02-28 23:45:00.000000000       0     -7204.000000   
 
         ev_charger_level_2_load.P  ev_charger_level_3_load.P  generator.P  \
 0                               0                          0  -117.000000   
 1                               0                

In [20]:
for i in range(len(df)):
    df[i] = resample(df[i])
df

[                     time  BESS.P  building_load.P  ev_charger_level_2_load.P  \
 0     2022-03-01 00:00:00     0.0     -8511.496333                        0.0   
 1     2022-03-01 00:15:00     0.0     -8800.405514                        0.0   
 2     2022-03-01 00:30:00     0.0     -8514.191421                        0.0   
 3     2022-03-01 00:45:00     0.0     -8801.013014                        0.0   
 4     2022-03-01 01:00:00     0.0     -8669.753653                        0.0   
 ...                   ...     ...              ...                        ...   
 35035 2023-02-28 22:45:00     0.0     -6952.002212                        0.0   
 35036 2023-02-28 23:00:00     0.0     -7045.998556                        0.0   
 35037 2023-02-28 23:15:00     0.0     -6965.001539                        0.0   
 35038 2023-02-28 23:30:00     0.0     -7092.000718                        0.0   
 35039 2023-02-28 23:45:00     0.0     -7204.000000                        0.0   
 
        ev_cha

In [21]:
for i in range(len(df)):
    df[i][df[i].select_dtypes(include=['number']).columns] /= 1000
df

[                     time  BESS.P  building_load.P  ev_charger_level_2_load.P  \
 0     2022-03-01 00:00:00     0.0        -8.511496                        0.0   
 1     2022-03-01 00:15:00     0.0        -8.800406                        0.0   
 2     2022-03-01 00:30:00     0.0        -8.514191                        0.0   
 3     2022-03-01 00:45:00     0.0        -8.801013                        0.0   
 4     2022-03-01 01:00:00     0.0        -8.669754                        0.0   
 ...                   ...     ...              ...                        ...   
 35035 2023-02-28 22:45:00     0.0        -6.952002                        0.0   
 35036 2023-02-28 23:00:00     0.0        -7.045999                        0.0   
 35037 2023-02-28 23:15:00     0.0        -6.965002                        0.0   
 35038 2023-02-28 23:30:00     0.0        -7.092001                        0.0   
 35039 2023-02-28 23:45:00     0.0        -7.204000                        0.0   
 
        ev_cha

Call the the function to label peaks

In [22]:
#df = clean_data(df, "Date", ['ServiceAccount', 'Date', 'Meter Number', 'Unit of Measurement'])
for i in range(len(df)):    
    df[i] = label_weekends(df[i], 'time')
    label_peaks(df[i], i)
    df[i] = df[i].reset_index(drop = True)
df

/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933

/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933

/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933

/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933441.py:173: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  selection = df[df['fun'] == 'Winter_Weekend'].between_time(wt_wkd_ofpk[begin],wt_wkd_ofpk[end], include_end=False)
/tmp/ipykernel_12432/34933441.py:176: FutureWarning: `include_start` and `include_end` are deprecated in favour of `inclusive`.
  df.loc[df[ww].between_time(wt_wkd_ofpk[begin], wt_wkd_ofpk[end], include_end=False).index, "Peak"] = "Off-Peak"
/tmp/ipykernel_12432/34933

[                     time  BESS.P  building_load.P  ev_charger_level_2_load.P  \
 0     2022-03-01 00:00:00     0.0        -8.511496                        0.0   
 1     2022-03-01 00:15:00     0.0        -8.800406                        0.0   
 2     2022-03-01 00:30:00     0.0        -8.514191                        0.0   
 3     2022-03-01 00:45:00     0.0        -8.801013                        0.0   
 4     2022-03-01 01:00:00     0.0        -8.669754                        0.0   
 ...                   ...     ...              ...                        ...   
 35035 2023-02-28 22:45:00     0.0        -6.952002                        0.0   
 35036 2023-02-28 23:00:00     0.0        -7.045999                        0.0   
 35037 2023-02-28 23:15:00     0.0        -6.965002                        0.0   
 35038 2023-02-28 23:30:00     0.0        -7.092001                        0.0   
 35039 2023-02-28 23:45:00     0.0        -7.204000                        0.0   
 
        ev_cha

# Find Enrgy and Power Values and Costs

## Seperate interval by billing month

In [23]:
billing = pd.read_excel("/home/lencon/Git_Research/summer_2023_conf_paper/Code/Microgrid_Data/billing_month.xlsx")
billing

billing_month
0     2022-03-01
1     2022-04-01
2     2022-05-01
3     2022-06-01
4     2022-07-01
5     2022-08-01
6     2022-09-01
7     2022-10-01
8     2022-11-01
9     2022-12-01
10    2023-01-01
11    2023-02-01
12    2023-03-01

In [24]:
billMonth = billing.billing_month
offset = pd.DateOffset(minutes=15)
timestamp_name = 'time'
month = {}
monthLength = len(billMonth) - 1
for i in range(len(df)):
    temp = {}
    for j in range (0,monthLength,1):
        end = billMonth[j + 1] - offset
        temp[j] = df[i][df[i][timestamp_name].between(billMonth[j], end)]
    month[i] = temp
month

{0: {0:                     time  BESS.P  building_load.P  ev_charger_level_2_load.P  \
  0    2022-03-01 00:00:00     0.0        -8.511496                        0.0   
  1    2022-03-01 00:15:00     0.0        -8.800406                        0.0   
  2    2022-03-01 00:30:00     0.0        -8.514191                        0.0   
  3    2022-03-01 00:45:00     0.0        -8.801013                        0.0   
  4    2022-03-01 01:00:00     0.0        -8.669754                        0.0   
  ...                  ...     ...              ...                        ...   
  2971 2022-03-31 22:45:00     0.0        -8.622674                        0.0   
  2972 2022-03-31 23:00:00     0.0        -8.616000                        0.0   
  2973 2022-03-31 23:15:00     0.0        -9.469182                        0.0   
  2974 2022-03-31 23:30:00     0.0        -9.966835                        0.0   
  2975 2022-03-31 23:45:00     0.0        -8.675649                        0.0   
  
       

## Find energy values (kWh) and energy costs

In [25]:
def energy(df, month, time_column = 'time', demand = 'Demand', cost = [False, False, False, False, False]): 
    # cost = [] vector must have five numeric elements/items, or be set to False if not 
    df = df.reset_index(drop=True)

    if len(month) != 0:
        monthLength = len(month) 
    else:
         monthLength = 0
            
    monthTitle = {}
    for i in range(0, monthLength, 1): # iterates through every billing month df
        monthTitle[i] = month[i][time_column].min().strftime('%b_%d_%Y') + ' to ' + month[i][time_column].max().strftime('%b_%d_%Y')

    columns = ['Billing Month', 'kiloWattHour Total', 'kiloWattHour Super Off-Peak', 'kiloWattHour Off-Peak', 'kiloWattHour Mid-Peak', 'kiloWattHour On-Peak']
    columns_cost = ['Total Energy Cost ($)', 'Super Off-Peak Energy Cost ($)', 'Off-Peak Energy Cost ($)', 'Mid-Peak Energy Cost ($)', 'On-Peak Energy Cost ($)']
    for j in range(5):
            if (type(cost[j]) == int or type(cost[j]) == float ):
                columns.append(columns_cost[j])
    
    col_len = int(len(columns))
    kiloWattHour = pd.DataFrame(np.zeros([monthLength, col_len])*np.nan, columns = columns)

    for i in range(0, monthLength, 1):
        month[i] = month[i].reset_index(drop=True)
        kiloWattHour['Billing Month'][i] = monthTitle[i]
        kiloWattHour['kiloWattHour Total'][i] = month[i][demand].sum() / 4
        kiloWattHour['kiloWattHour Super Off-Peak'][i] = month[i][demand][month[i].Peak == 'Super Off-Peak'].sum() / 4
        kiloWattHour['kiloWattHour Off-Peak'][i] = month[i][demand][month[i].Peak == 'Off-Peak'].sum() / 4
        kiloWattHour['kiloWattHour Mid-Peak'][i] = month[i][demand][month[i].Peak == 'Mid-Peak'].sum() / 4
        kiloWattHour['kiloWattHour On-Peak'][i] = month[i][demand][month[i].Peak == 'On-Peak'].sum() / 4
        
        for k in range(5):
            if (type(cost[k]) == int or type(cost[k]) == float ):
                kiloWattHour[columns_cost[k]][i] = kiloWattHour[columns[k + 1]][i]  *  cost[k]
                

    kiloWattHour.loc[len(kiloWattHour)] = np.nan
    kiloWattHour = kiloWattHour.shift()
    kiloWattHour['Billing Month'][0] = 'Entire Interval'
    kiloWattHour['kiloWattHour Total'][0] = df[demand].sum() / 4
    kiloWattHour['kiloWattHour Super Off-Peak'][0] = df[demand][df.Peak == 'Super Off-Peak'].sum() / 4
    kiloWattHour['kiloWattHour Off-Peak'][0] = df[demand][df.Peak == 'Off-Peak'].sum() / 4
    kiloWattHour['kiloWattHour Mid-Peak'][0] = df[demand][df.Peak == 'Mid-Peak'].sum() / 4
    kiloWattHour['kiloWattHour On-Peak'][0] = df[demand][df.Peak == 'On-Peak'].sum() / 4
    for l in range(0, 5, 1):
        
        if (type(cost[l]) == int or type(cost[l]) == float ):
            kiloWattHour[columns_cost[l]][0] = kiloWattHour[columns[l + 1]][0] *  cost[l]
                

    return kiloWattHour 

In [31]:
sav = pd.DataFrame(np.zeros((8,5), dtype=int), columns = ['Scenario', 'Demand Charges', 'Energy Charges', 'Emissions', '% Emissions Savings']) 
sav['Scenario'] = np.array([1,2,3,4,5,6,7,8])
sav

Scenario  Demand Charges  Energy Charges  Emissions  % Emissions Savings
0         1               0               0          0                    0
1         2               0               0          0                    0
2         3               0               0          0                    0
3         4               0               0          0                    0
4         5               0               0          0                    0
5         6               0               0          0                    0
6         7               0               0          0                    0
7         8               0               0          0                    0

In [36]:
cost = [[-0.1242, False, False, False, False], [-0.1242, False, False, False, False], [-0.1242, False, False, False, False], [-0.1242, False, False, False, False], [-0.1242, False, False, False, False], [-0.1242, False, False, False, False], [-0.1242, False, False, False, False], [-0.1242, False, False, False, False]]
kiloWattHour_load = {}
for i in range(len(df)):
    kiloWattHour_load[i] = energy(df[i],month[i], time_column = 'time', demand = 'grid.sou.S[1]', cost = cost[i])

/tmp/ipykernel_12432/2952468949.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWattHour['kiloWattHour Total'][i] = month[i][demand].sum() / 4
/tmp/ipykernel_12432/2952468949.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWattHour['kiloWattHour Super Off-Peak'][i] = month[i][demand][month[i].Peak == 'Super Off-Peak'].sum() / 4
/tmp/ipykernel_12432/2952468949.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWa

/tmp/ipykernel_12432/2952468949.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWattHour['Billing Month'][0] = 'Entire Interval'
/tmp/ipykernel_12432/2952468949.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWattHour['kiloWattHour Total'][0] = df[demand].sum() / 4
/tmp/ipykernel_12432/2952468949.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWattHour['kiloWattHour Super Off-Peak'][0] = df[demand][df.Peak ==

/tmp/ipykernel_12432/2952468949.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWattHour['kiloWattHour Total'][i] = month[i][demand].sum() / 4
/tmp/ipykernel_12432/2952468949.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWattHour['kiloWattHour Super Off-Peak'][i] = month[i][demand][month[i].Peak == 'Super Off-Peak'].sum() / 4
/tmp/ipykernel_12432/2952468949.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kiloWa

In [37]:
kiloWattHour_load

{0:                  Billing Month  kiloWattHour Total  \
 0              Entire Interval        19061.503215   
 1   Mar_01_2022 to Mar_31_2022         7406.302998   
 2   Apr_01_2022 to Apr_30_2022           10.315263   
 3   May_01_2022 to May_31_2022         1318.135865   
 4   Jun_01_2022 to Jun_30_2022        -4374.777642   
 5   Jul_01_2022 to Jul_31_2022         5883.835677   
 6   Aug_01_2022 to Aug_31_2022          606.886902   
 7   Sep_01_2022 to Sep_30_2022        -1216.729292   
 8   Oct_01_2022 to Oct_31_2022         1718.612907   
 9   Nov_01_2022 to Nov_30_2022         3052.716715   
 10  Dec_01_2022 to Dec_31_2022           78.553488   
 11  Jan_01_2023 to Jan_31_2023         1717.687289   
 12  Feb_01_2023 to Feb_28_2023         2859.963046   
 
     kiloWattHour Super Off-Peak  kiloWattHour Off-Peak  kiloWattHour Mid-Peak  \
 0                           0.0          -26333.507060           41147.430727   
 1                           0.0           -1074.778918      

In [38]:
energy_cost = []
for i in range(3):
    energy_cost.append(kiloWattHour_load[i][1:]['Total Energy Cost ($)'].sum())
for i in range(3,len(df)):
    energy_cost.append(kiloWattHour_load[i][1:]['Off-Peak Energy Cost ($)'].sum() + kiloWattHour_load[i][1:]['Mid-Peak Energy Cost ($)'].sum() + kiloWattHour_load[i][1:]['On-Peak Energy Cost ($)'].sum())

sav['Energy Charges'] = np.array(energy_cost).astype(int)
sav

KeyError: 'Off-Peak Energy Cost ($)'

## Find power values (kW) and demand costs

In [28]:
def max_peak(df, month, time_column = 'time', demand = 'Demand', cost = [False, False, False, False, False]):
    # cost = [] vector must have five numeric elements/items, or be set to False if not 
    df = df.reset_index(drop=True)

    if len(month) != 0:
        monthLength = len(month) 
    else:
         monthLength = 0

    monthTitle = {}
    for i in range(0, monthLength, 1): # iterates through every billing month df
        monthTitle[i] = month[i][time_column].min().strftime('%b_%d_%Y') + ' to ' + month[i][time_column].max().strftime('%b_%d_%Y')

    columns = ['Billing Month', 'max_peak Total', 'max_peak Super Off-Peak', 'max_peak Off-Peak', 'max_peak Mid-Peak', 'max_peak On-Peak']
    columns_cost = ['Total Demand Cost ($)', 'Super Off-Peak Demand Cost ($)', 'Off-Peak Demand Cost ($)', 'Mid-Peak Demand Cost ($)', 'On-Peak Demand Cost ($)']
    for j in range(5):
            if (type(cost[j]) == int or type(cost[j]) == float ):
                columns.append(columns_cost[j])
    col_len = int(len(columns))
    max_peak = pd.DataFrame(np.zeros([monthLength, col_len])*np.nan, columns = columns)
    for i in range(0, monthLength, 1):
        month[i] = month[i].reset_index(drop=True)
        max_peak['Billing Month'][i] = monthTitle[i]
        max_peak['max_peak Total'][i] = month[i][demand].min()
        max_peak['max_peak Super Off-Peak'][i] = month[i][demand][month[i].Peak == 'Super Off-Peak'].min()
        max_peak['max_peak Off-Peak'][i] = month[i][demand][month[i].Peak == 'Off-Peak'].min()
        max_peak['max_peak Mid-Peak'][i] = month[i][demand][month[i].Peak == 'Mid-Peak'].min()
        max_peak['max_peak On-Peak'][i] = month[i][demand][month[i].Peak == 'On-Peak'].min()
        for k in range(5):
            if (type(cost[k]) == int or type(cost[k]) == float ):
                max_peak[columns_cost[k]][i] = max_peak[columns[k + 1]][i]  *  cost[k]
                
    max_peak.loc[len(max_peak)] = np.nan
    max_peak = max_peak.shift()
    max_peak['Billing Month'][0] = 'Entire Interval'
    max_peak['max_peak Total'][0] = df[demand].min()
    max_peak['max_peak Super Off-Peak'][0] = df[demand][df.Peak == 'Super Off-Peak'].min()
    max_peak['max_peak Off-Peak'][0] = df[demand][df.Peak == 'Off-Peak'].min()
    max_peak['max_peak Mid-Peak'][0] = df[demand][df.Peak == 'Mid-Peak'].min()
    max_peak['max_peak On-Peak'][0] = df[demand][df.Peak == 'On-Peak'].min()
    
    for l in range(0, 5, 1):    
        if (type(cost[l]) == int or type(cost[l]) == float ):
            max_peak[columns_cost[l]][0] = max_peak[columns[l + 1]][0] *  cost[l]

    return max_peak

In [29]:
cost = [[-12.48, False, False, False, False], [-12.48, False, False, False, False],
                 [-12.48, False, False, False, False], [False, False, -1.85, -3.69, -7.38], [False, False, -0, -3.75, -10], [False, False, -0, -0, -18.11]]
max_peak_load = {}
for i in range(len(df)):
    max_peak_load[i] = max_peak(df[i],month[i],time_column = 'time', demand = 'grid.sou.S[1]', cost = cost[i])
max_peak_load

/tmp/ipykernel_10836/1952285755.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  max_peak['max_peak Total'][i] = month[i][demand].min()
/tmp/ipykernel_10836/1952285755.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  max_peak['max_peak Super Off-Peak'][i] = month[i][demand][month[i].Peak == 'Super Off-Peak'].min()
/tmp/ipykernel_10836/1952285755.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  max_peak['max_peak Off-Peak'][

/tmp/ipykernel_10836/1952285755.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  max_peak['Billing Month'][0] = 'Entire Interval'
/tmp/ipykernel_10836/1952285755.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  max_peak['max_peak Total'][0] = df[demand].min()
/tmp/ipykernel_10836/1952285755.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  max_peak['max_peak Super Off-Peak'][0] = df[demand][df.Peak == 'Super Off-Peak'].min()

{0:                  Billing Month  max_peak Total  max_peak Super Off-Peak  \
 0              Entire Interval  -139240.878070                      NaN   
 1   Mar_01_2022 to Mar_31_2022  -108523.647030                      NaN   
 2   Apr_01_2022 to Apr_30_2022  -108370.279113                      NaN   
 3   May_01_2022 to May_31_2022  -119241.695156                      NaN   
 4   Jun_01_2022 to Jun_30_2022  -132007.156339                      NaN   
 5   Jul_01_2022 to Jul_31_2022  -131364.678944                      NaN   
 6   Aug_01_2022 to Aug_31_2022  -139240.878070                      NaN   
 7   Sep_01_2022 to Sep_30_2022  -127901.210035                      NaN   
 8   Oct_01_2022 to Oct_31_2022  -106864.548225                      NaN   
 9   Nov_01_2022 to Nov_30_2022   -99755.066292                      NaN   
 10  Dec_01_2022 to Dec_31_2022   -96248.650790                      NaN   
 11  Jan_01_2023 to Jan_31_2023  -100335.642058                      NaN   
 12  Feb_

In [30]:
demand_cost = []
for i in range(3):
    demand_cost.append(max_peak_load[i][1:]['Total Demand Cost ($)'].sum())
for i in range(3,len(df)):
    demand_cost.append(max_peak_load[i][1:]['Off-Peak Demand Cost ($)'].sum() + max_peak_load[i][1:]['Mid-Peak Demand Cost ($)'].sum() + max_peak_load[i][1:]['On-Peak Demand Cost ($)'].sum())

sav['Demand Charges'] = np.array(demand_cost).astype(int)
sav

Scenario  Demand Charges  Energy Charges  Emissions  % Emissions Savings
0         1        17090156        32212807          0                    0
1         2        14460338         7059192          0                    0
2         3        12907881         8768493          0                    0
3         4        15297905         6584168          0                    0
4         5        14394397         2308064          0                    0
5         6         7127364        -1420383          0                    0

## Emissions output

In [32]:
er = pd.read_csv('/home/lencon/Git_Research/summer_2023_conf_paper/Code/Microgrid_Data/CAISOdata.csv')
er['emissons_rate'] = er[['imports_co2', 'natgas_co2', 'biogas_co2',
       'biomass_co2', 'geothermal_co2', 'coal_co2']].sum(axis=1) / er[['wind_curtail_MW', 'solar_curtail_MW', 'solar_MW', 'wind_MW',
       'geothermal_MW', 'biomass_MW', 'biogas_MW', 'sm_hydro_MW', 'battery_MW',
       'renewable_MW', 'natgas_MW', 'lg_hydro_MW', 'imports_MW', 'nuclear_MW',
       'coal_MW']].sum(axis=1)
er.date = pd.to_datetime(er.date.astype(str) + ' ' + er['5min_ending'].astype(str))
er['date'] = er['date'] + pd.DateOffset(years = 3)
er

date  month   day  weekday  hour  interval 5min_ending  \
0      2021-04-12 00:00:00    4.0  12.0      4.0   0.0       1.0       00:00   
1      2021-04-12 00:05:00    4.0  12.0      4.0   0.0       2.0       00:05   
2      2021-04-12 00:10:00    4.0  12.0      4.0   0.0       3.0       00:10   
3      2021-04-12 00:15:00    4.0  12.0      4.0   0.0       4.0       00:15   
4      2021-04-12 00:20:00    4.0  12.0      4.0   0.0       5.0       00:20   
...                    ...    ...   ...      ...   ...       ...         ...   
210544 2023-04-12 23:35:00    4.0  12.0      0.0  23.0       8.0       23:35   
210545 2023-04-12 23:40:00    4.0  12.0      0.0  23.0       9.0       23:40   
210546 2023-04-12 23:45:00    4.0  12.0      0.0  23.0      10.0       23:45   
210547 2023-04-12 23:50:00    4.0  12.0      0.0  23.0      11.0       23:50   
210548 2023-04-12 23:55:00    4.0  12.0      0.0  23.0      12.0       23:55   

        demand_DayAF  demand_HourAF  demand_actual  ...  nuclear_MW  coal_MW  \
0            22555.0        21942.0        21825.0  ...      1616.0      2.0   
1            20916.0        21661.0        21694.0  ...      1616.0      3.0   
2            20916.0        21661.0        21619.0  ...      1617.0      3.0   
3            20916.0        21661.0        21556.0  ...      1618.0      4.0   
4            20916.0        21494.0        21459.0  ...      1617.0      4.0   
...              ...            ...            ...  ...         ...      ...   
210544       19047.0        19314.0        19286.0  ...      2260.0     17.0   
210545       19047.0        19314.0        19193.0  ...      2261.0     17.0   
210546       19047.0        19314.0        19103.0  ...      2261.0     17.0   
210547       19047.0        19044.0        19002.0  ...      2261.0     16.0   
210548       19047.0        19044.0        18948.0  ...      2261.0     16.0   

        other_MW  imports_co2  natgas_co2  biogas_co2  biomass_co2  \
0            0.0       2714.0      3007.0       146.0        123.0   
1            0.0       2666.0      2992.0       147.0        123.0   
2            0.0       2586.0      3070.0       146.0        121.0   
3            0.0       2658.0      3164.0       144.0        121.0   
4            0.0       2629.0      3097.0       142.0        119.0   
...          ...          ...         ...         ...          ...   
210544       0.0       2183.0      2756.0       119.0        124.0   
210545       0.0       2137.0      2784.0       119.0        123.0   
210546       0.0       2115.0      2767.0       118.0        122.0   
210547       0.0       2075.0      2761.0       118.0        122.0   
210548       0.0       2048.0      2754.0       118.0        117.0   

        geothermal_co2  coal_co2  emissons_rate  
0                  8.0       2.0       0.215285  
1                  8.0       2.0       0.214221  
2                  8.0       3.0       0.212346  
3                  8.0       3.0       0.217328  
4                  8.0       3.0       0.213672  
...                ...       ...            ...  
210544             8.0      13.0       0.221376  
210545             8.0      13.0       0.222089  
210546             8.0      13.0       0.221442  
210547             8.0      13.0       0.220850  
210548             8.0      13.0       0.219094  

[210549 rows x 34 columns]

In [33]:
ers = resample(er, time_column = 'date')
ers = ers[ers.date.between('03/01/2022', '03/01/2023', inclusive = 'left')].reset_index(drop=True)
ers

date  month   day  weekday  hour  interval  demand_DayAF  \
0     2022-03-01 00:00:00    3.0   1.0      5.0   0.0       2.0  21233.666667   
1     2022-03-01 00:15:00    3.0   1.0      5.0   0.0       5.0  20864.000000   
2     2022-03-01 00:30:00    3.0   1.0      5.0   0.0       8.0  20864.000000   
3     2022-03-01 00:45:00    3.0   1.0      5.0   0.0      11.0  20864.000000   
4     2022-03-01 01:00:00    3.0   1.0      5.0   1.0       2.0  20360.000000   
...                   ...    ...   ...      ...   ...       ...           ...   
35035 2023-02-28 22:45:00    2.0  28.5      5.5  22.0      11.0  22666.000000   
35036 2023-02-28 23:00:00    2.0  28.5      5.5  23.0       2.0  21773.333333   
35037 2023-02-28 23:15:00    2.0  28.5      5.5  23.0       5.0  21327.000000   
35038 2023-02-28 23:30:00    2.0  28.5      5.5  23.0       8.0  21327.000000   
35039 2023-02-28 23:45:00    2.0  28.5      5.5  23.0      11.0  21327.000000   

       demand_HourAF  demand_actual    demand_net  ...   nuclear_MW  \
0       20817.666667   20718.333333  17999.000000  ...  1132.000000   
1       20616.666667   20504.000000  17759.333333  ...  1132.000000   
2       20371.333333   20286.000000  17521.666667  ...  1132.333333   
3       20116.333333   20043.000000  17317.666667  ...  1131.666667   
4       19898.666667   19914.666667  17259.333333  ...  1131.666667   
...              ...            ...           ...  ...          ...   
35035   22273.000000   22268.666667  20390.000000  ...  2263.166667   
35036   21930.666667   21878.000000  20001.500000  ...  2263.000000   
35037   21618.666667   21551.666667  19599.500000  ...  2263.000000   
35038   21319.500000   21250.666667  19254.333333  ...  2262.500000   
35039   21022.333333   20921.000000  18964.666667  ...  2262.833333   

         coal_MW  other_MW  imports_co2   natgas_co2  biogas_co2  biomass_co2  \
0      19.666667       0.0  1407.000000  3807.000000  119.333333   119.000000   
1      20.000000       0.0  1439.666667  3710.333333  120.666667   120.333333   
2      20.333333       0.0  1404.333333  3695.666667  121.333333   119.666667   
3      20.000000       0.0  1366.000000  3676.666667  122.333333   120.666667   
4      19.000000       0.0  1312.333333  3729.333333  122.666667   120.666667   
...          ...       ...          ...          ...         ...          ...   
35035  17.333333       0.0  3931.833333  2751.333333  111.666667   160.166667   
35036  17.833333       0.0  3854.166667  2702.166667  112.000000   162.666667   
35037  17.500000       0.0  3773.833333  2609.666667  112.166667   161.333333   
35038  17.666667       0.0  3821.833333  2444.500000  112.833333   156.833333   
35039  17.666667       0.0  3860.166667  2323.666667  112.500000   159.833333   

       geothermal_co2   coal_co2  emissons_rate  
0                 9.0  14.666667       0.211547  
1                 9.0  15.000000       0.211444  
2                 9.0  15.000000       0.210934  
3                 9.0  15.333333       0.211307  
4                 9.0  14.333333       0.213443  
...               ...        ...            ...  
35035             7.5  13.500000       0.271135  
35036             7.5  13.666667       0.270414  
35037             7.5  13.500000       0.266208  
35038             7.5  13.500000       0.264140  
35039             7.5  13.666667       0.264821  

[35040 rows x 33 columns]

In [34]:
def get_emission(df, er):
    df['grid.sou.S[1]'][df['grid.sou.S[1]'] > 0] = 0
    e = df['grid.sou.S[1]'] * er.emissons_rate * -0.00025
    e = e.sum()
    return e
emissions = []
for i in range(len(df)):
    emissions.append(get_emission(df[i], ers))
sav['Emissions'] = np.array(emissions).astype(int)
sav

/tmp/ipykernel_10836/860118804.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['grid.sou.S[1]'][df['grid.sou.S[1]'] > 0] = 0


Scenario  Demand Charges  Energy Charges  Emissions  % Emissions Savings
0         1        17090156        32212807      47259                    0
1         2        14460338         7059192      30207                    0
2         3        12907881         8768493      26711                    0
3         4        15297905         6584168      34603                    0
4         5        14394397         2308064      34095                    0
5         6         7127364        -1420383      35928                    0

In [35]:
def day_time(freq = '1min'):
    # Create the number on intervals during the day
    time_array = pd.date_range('0:00', '23:59:59', freq=freq).strftime('%H:%M')
    return(time_array)

def time_sep_label(df, time_column = 'time', resample_rate = '1T', value_column = 'value'):
    # Ensure time column is in datetime format
    df[time_column] = pd.to_datetime(df[time_column])
    # Set time column as index
    df = df.set_index(df[time_column])
    # Remove time column from dataframe since it is now the index
    df = df.drop(columns = [time_column])
    # Clean up and resample missing data 
    df = df.resample(resample_rate).mean()
    # Extract the time period ths user wants in a day as an integer
    resample_rate_int =  int(resample_rate.rstrip(resample_rate[-1]))
    # Change '1T' to '1min' Call the daytime function to produce the time intervals
    time_array = day_time(str(resample_rate_int) + 'min')
    # Create a new column for labeling each row 
    df['time_interval_label'] = np.nan
    # Declare the list for indexes for ever interval
    avg_day = []
    # Extract the indexes for ever interval
    for i in range(len(time_array) - 1):
        avg_day.append(df[value_column].between_time(time_array[i], time_array[i + 1], inclusive = 'left').mean())
    return[time_array, avg_day]

In [36]:
def get_emission(df, er):
    df['grid.sou.S[1]'][df['grid.sou.S[1]'] > 0] = 0
    e = df['grid.sou.S[1]'] * er.emissons_rate * -0.00025
    return e
edf = pd.DataFrame({'time' : df[i].time})
for i in range(len(df)):
    edf[str(i)] = (get_emission(df[i], ers))
edf

/tmp/ipykernel_10836/3387705475.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['grid.sou.S[1]'][df['grid.sou.S[1]'] > 0] = 0
/tmp/ipykernel_10836/3387705475.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['grid.sou.S[1]'][df['grid.sou.S[1]'] > 0] = 0
/tmp/ipykernel_10836/3387705475.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['grid.sou.S[1]'][df['grid.sou.S[1]'] > 0] = 0
/tmp/ipykernel_10836/3387705475.py:2: Se

time         0         1         2         3         4  \
0     2022-03-01 00:00:00  0.737941  0.744142  0.744142  0.744142  0.744142   
1     2022-03-01 00:15:00  0.743428  0.749676  0.749676  0.749676  0.749676   
2     2022-03-01 00:30:00  0.738278  0.744553  0.744553  0.744553  0.744553   
3     2022-03-01 00:45:00  0.749326  0.755592  0.755592  0.755592  0.755592   
4     2022-03-01 01:00:00  0.753186  0.759429  0.759429  0.759429  0.759429   
...                   ...       ...       ...       ...       ...       ...   
35035 2023-02-28 22:45:00  1.223497  1.232105  1.232105  1.232105  1.232105   
35036 2023-02-28 23:00:00  1.213077  1.221663  1.221663  1.221663  1.221663   
35037 2023-02-28 23:15:00  1.208051  1.216569  1.216569  1.216569  1.216569   
35038 2023-02-28 23:30:00  1.205669  1.214122  1.214122  1.214122  1.214122   
35039 2023-02-28 23:45:00  1.200633  1.209173  1.209173  1.209173  1.209173   

              5  
0      0.744142  
1      0.749676  
2      0.744553  
3      0.755592  
4      0.759429  
...         ...  
35035  1.232105  
35036  1.221663  
35037  1.216569  
35038  1.214122  
35039  1.209173  

[35040 rows x 7 columns]

In [37]:
avg_emissions = pd.DataFrame()
for i in range(len(df)):
    time_array, avg_day = time_sep_label(edf, resample_rate = '60T', value_column = str(i))
    avg_emissions[str(i)] = avg_day
avg_emissions

0         1         2         3         4         5
0   1.006901  1.002441  0.939066  1.008847  1.007742  1.060763
1   0.954759  0.954442  0.900668  0.956392  0.957322  0.973546
2   0.960186  0.964556  0.912647  0.966157  0.974318  0.963655
3   1.005242  1.010781  0.948267  1.020000  1.009725  1.027566
4   1.075568  1.067643  0.997684  1.093068  1.088244  1.099333
5   1.208887  1.252195  1.106814  1.237730  1.235197  1.247176
6   1.410867  1.342241  1.175417  1.403804  1.397265  1.373853
7   1.584028  1.150745  0.992742  1.402371  1.447244  1.334446
8   1.378650  0.499535  0.470260  0.978513  1.175201  0.957297
9   1.357088  0.287431  0.294715  0.887773  1.148203  0.933670
10  1.273535  0.152347  0.174854  0.830651  0.453845  0.775578
11  1.329170  0.143321  0.169228  0.708669  0.462847  0.837141
12  1.330404  0.137356  0.155933  0.133685  0.453547  0.912208
13  1.385779  0.163720  0.162498  0.153100  0.154201  0.916088
14  1.436796  0.198002  0.199714  0.187630  0.174415  0.887459
15  1.540893  0.330618  0.296663  0.291557  0.211174  0.754044
16  1.672642  0.649464  0.530772  0.509403  0.301742  0.159833
17  1.759793  1.041819  0.859021  0.977901  0.879853  0.257088
18  1.786714  1.442235  1.139417  1.729141  1.379612  0.716429
19  1.780949  1.711864  1.374152  1.843907  1.887110  1.464394
20  1.619298  1.637826  1.342845  1.721881  1.915629  1.584266
21  1.360615  1.364473  1.169015  1.428984  1.427452  1.689140
22  1.175193  1.179344  1.055267  1.209066  1.199972  1.517168

In [38]:
sav['% Emissions Savings'] = (sav['Emissions'].max() - sav['Emissions']) / sav['Emissions'].max() * 100
sav['% Emissions Savings'] = sav['% Emissions Savings'].astype(int)
sav

Scenario  Demand Charges  Energy Charges  Emissions  % Emissions Savings
0         1        17090156        32212807      47259                    0
1         2        14460338         7059192      30207                   36
2         3        12907881         8768493      26711                   43
3         4        15297905         6584168      34603                   26
4         5        14394397         2308064      34095                   27
5         6         7127364        -1420383      35928                   23

In [39]:
sav.to_latex('/home/sigi_laptop/Documents/Research/NAPS_2023/Conference_Paper/LaTeX/Table/kw_kwh_co2.tex', index = False)

/tmp/ipykernel_18272/2377164834.py:1: FutureWarning: In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.
  sav.to_latex('/home/sigi_laptop/Documents/Research/NAPS_2023/Conference_Paper/LaTeX/Table/kw_kwh_co2.tex', index = False)


## Plot Data 

In [39]:
import os
os.chdir('/home/lencon/Git_Research/summer_2023_conf_paper/Conference_Paper/LaTeX/Fig')

In [49]:
def plot_graph(x_data, y_data, line_name, title, x_title, y_title, filename, line_color, fig_show = False):
    # Define the figure
    fig = go.Figure()
    # Add data to figure
    for i in range(0, len(x_data), 1):
        fig.add_trace(go.Scattergl(x=x_data[i], y=y_data[i], name= line_name[i], line_color = line_color[i]))
            
    # Create Layout for the Html
    
    fig.update_layout(
        title=go.layout.Title(
            text= title,
            xref="paper",
            x=0.5
        ),
        xaxis=go.layout.XAxis(
            title=go.layout.xaxis.Title(
                text=x_title,
            ),
            rangeslider=dict(
                visible=True
            )
        ),
        yaxis=go.layout.YAxis(
            title=go.layout.yaxis.Title(
                text=y_title,
            )
        ),
        plot_bgcolor = "white"
    )
    
    fig.write_html((filename + '.html'), include_mathjax='cdn')
    fig = go.Figure()
    # Add data to figure
    for i in range(0, len(x_data), 1):
        fig.add_trace(go.Scatter(x=x_data[i], y=y_data[i], name= line_name[i], line_color = line_color[i]))
    fig.update_layout(
        title=go.layout.Title(
            text= title,
            xref="paper",
            x=0.5
        ),
        xaxis=go.layout.XAxis(
            title=go.layout.xaxis.Title(
                text=x_title,
            ),
            rangeslider=dict(
                visible=False
            )
        ),
        yaxis=go.layout.YAxis(
            title=go.layout.yaxis.Title(
                text=y_title,
            )
        ),
        plot_bgcolor = "white"
    )
    fig.write_image(filename + '.svg', engine = 'orca')
    fig.write_image(filename + '.pdf', engine = 'orca')
    # fig.write_image(filename + '.png') Do not use png in your code this is only an example to compare png to vector images
    if fig_show:
        fig.show()

In [42]:
#create title for plots
#create filename for plots
site_name = ["Scenario 1", "Scenario 2", "Scenario 3", "Scenario 4", "Scenario 5", "Scenario 6"]
plot_type = "Microgrid Output"
month_title = {}
for i in range(len(df)):
    temp = {}
    for j in range (0,len(month[i])):
        temp[j] = site_name[i] + "<br>" + plot_type + "<br>From: " +  month[i][j].time.min().strftime('%B %d, %Y') + " to " + month[i][j].time.max().strftime('%B %d, %Y') 
    month_title[i] = temp 
month_title

{0: {0: 'Scenario 1<br>Microgrid Output<br>From: March 01, 2022 to March 31, 2022',
  1: 'Scenario 1<br>Microgrid Output<br>From: April 01, 2022 to April 30, 2022',
  2: 'Scenario 1<br>Microgrid Output<br>From: May 01, 2022 to May 31, 2022',
  3: 'Scenario 1<br>Microgrid Output<br>From: June 01, 2022 to June 30, 2022',
  4: 'Scenario 1<br>Microgrid Output<br>From: July 01, 2022 to July 31, 2022',
  5: 'Scenario 1<br>Microgrid Output<br>From: August 01, 2022 to August 31, 2022',
  6: 'Scenario 1<br>Microgrid Output<br>From: September 01, 2022 to September 30, 2022',
  7: 'Scenario 1<br>Microgrid Output<br>From: October 01, 2022 to October 31, 2022',
  8: 'Scenario 1<br>Microgrid Output<br>From: November 01, 2022 to November 30, 2022',
  9: 'Scenario 1<br>Microgrid Output<br>From: December 01, 2022 to December 31, 2022',
  10: 'Scenario 1<br>Microgrid Output<br>From: January 01, 2023 to January 31, 2023',
  11: 'Scenario 1<br>Microgrid Output<br>From: February 01, 2023 to February 28, 20

In [43]:
#create filename for plots
site_name = ["Scenario_1", "Scenario_2", "Scenario_3", "Scenario_4", "Scenario_5", "Scenario_6"]
plot_type = "Mg_Output"
filename_list = {}
for i in range(len(df)):
    temp = {}
    for j in range (0,len(month[i])):
        temp[j] = str(j) + '_' + site_name[i] + '_' + plot_type + '_' + month[i][j].time.min().strftime('%b_%d_%Y') + "_to_" + month[i][j].time.max().strftime('%b_%d_%Y') 
    filename_list[i] = temp
filename_list

{0: {0: '0_Scenario_1_Mg_Output_Mar_01_2022_to_Mar_31_2022',
  1: '1_Scenario_1_Mg_Output_Apr_01_2022_to_Apr_30_2022',
  2: '2_Scenario_1_Mg_Output_May_01_2022_to_May_31_2022',
  3: '3_Scenario_1_Mg_Output_Jun_01_2022_to_Jun_30_2022',
  4: '4_Scenario_1_Mg_Output_Jul_01_2022_to_Jul_31_2022',
  5: '5_Scenario_1_Mg_Output_Aug_01_2022_to_Aug_31_2022',
  6: '6_Scenario_1_Mg_Output_Sep_01_2022_to_Sep_30_2022',
  7: '7_Scenario_1_Mg_Output_Oct_01_2022_to_Oct_31_2022',
  8: '8_Scenario_1_Mg_Output_Nov_01_2022_to_Nov_30_2022',
  9: '9_Scenario_1_Mg_Output_Dec_01_2022_to_Dec_31_2022',
  10: '10_Scenario_1_Mg_Output_Jan_01_2023_to_Jan_31_2023',
  11: '11_Scenario_1_Mg_Output_Feb_01_2023_to_Feb_28_2023'},
 1: {0: '0_Scenario_2_Mg_Output_Mar_01_2022_to_Mar_31_2022',
  1: '1_Scenario_2_Mg_Output_Apr_01_2022_to_Apr_30_2022',
  2: '2_Scenario_2_Mg_Output_May_01_2022_to_May_31_2022',
  3: '3_Scenario_2_Mg_Output_Jun_01_2022_to_Jun_30_2022',
  4: '4_Scenario_2_Mg_Output_Jul_01_2022_to_Jul_31_2022',
  5

In [50]:
x_title = "Time"
y_title = "Demand (kW)"
line_name = ["BESS", "Solar", "Grid Meter (Net Load)"]
line_color = ["deepskyblue", "red", "green"]
for i in range (0,len(df)):
    for j in range(0, len(month[i])):
        x_data = [month[i][j].time] * 3
        y_data = [month[i][j]["BESS.P"], month[i][j]["generator.P"], month[i][j]["grid.sou.S[1]"]]
        title = month_title[i][j]
        filename = filename_list[i][j]
        plot_graph(x_data, y_data, line_name, title, x_title, y_title, filename, line_color)

Fontconfig warning: "/usr/share/fontconfig/conf.avail/05-reset-dirs-sample.conf", line 6: unknown element "reset-dirs"
[18517:0812/165739.073835:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165744.279905:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165744.901690:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165745.527438:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165746.138453:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165746.747814:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID

[18517:0812/165815.499315:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165816.122787:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165816.820869:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165817.430744:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165818.053684:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165818.655414:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/165819.264368:ERROR:buffer_manager.cc(488)] [.

In [52]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(
    rows=3, cols=2,
    subplot_titles=("Scenario 1", "Scenario 2", "Scenario 3", "Scenario 4", "Scenario 5", "Scenario 6"))

# fig.add_trace(go.Scatter(x=month[0][3].time , y=month[0][3]["BESS.P"]),
#               row=1, col=1)

# fig.add_trace(go.Scatter(x=month[1][3].time , y=month[1][3]["BESS.P"]),
#               row=1, col=2)
fig.add_trace(go.Scatter(x=month[0][3].time , y=month[0][3]["grid.sou.S[1]"], name = "Grid Meter (Net Load)", legendgroup = '0'),
              row=1, col=1)

fig.add_trace(go.Scatter(x=month[1][3].time , y=month[1][3]["grid.sou.S[1]"], name = "Grid Meter (Net Load)", legendgroup = '1'),
              row=1, col=2)

fig.add_trace(go.Scatter(x=month[2][3].time , y=month[2][3]["grid.sou.S[1]"], name = "Grid Meter (Net Load)", legendgroup = '2'),
              row=2, col=1)

fig.add_trace(go.Scatter(x=month[3][3].time , y=month[3][3]["grid.sou.S[1]"], name = "Grid Meter (Net Load)", legendgroup = '3'),
              row=2, col=2)

fig.add_trace(go.Scatter(x=month[4][3].time , y=month[4][3]["grid.sou.S[1]"], name = "Grid Meter (Net Load)", legendgroup = '4'),
              row=3, col=1)

fig.add_trace(go.Scatter(x=month[5][3].time , y=month[5][3]["grid.sou.S[1]"], name = "Grid Meter (Net Load)", legendgroup = '5'),
              row=3, col=2)
#################
# fig.add_trace(go.Scatter(x=month[0][3].time , y=month[0][3]["generator.P"], name = "Solar", legendgroup = '0'),
#               row=1, col=1)

fig.add_trace(go.Scatter(x=month[1][3].time , y=month[1][3]["generator.P"], name = "Solar", legendgroup = '1'),
              row=1, col=2)

fig.add_trace(go.Scatter(x=month[2][3].time , y=month[2][3]["generator.P"], name = "Solar", legendgroup = '2'),
              row=2, col=1)

fig.add_trace(go.Scatter(x=month[3][3].time , y=month[3][3]["generator.P"], name = "Solar", legendgroup = '3'),
              row=2, col=2)

fig.add_trace(go.Scatter(x=month[4][3].time , y=month[4][3]["generator.P"], name = "Solar", legendgroup = '4'),
              row=3, col=1)

fig.add_trace(go.Scatter(x=month[5][3].time , y=month[5][3]["generator.P"], name = "Solar", legendgroup = '5'),
              row=3, col=2)
###############
fig.add_trace(go.Scatter(x=month[2][3].time , y=month[2][3]["BESS.P"], name = "BESS", legendgroup = '2'),
              row=2, col=1)

fig.add_trace(go.Scatter(x=month[3][3].time , y=month[3][3]["BESS.P"], name = "BESS", legendgroup = '3'),
              row=2, col=2)

fig.add_trace(go.Scatter(x=month[4][3].time , y=month[4][3]["BESS.P"], name = "BESS", legendgroup = '4'),
              row=3, col=1)

fig.add_trace(go.Scatter(x=month[5][3].time , y=month[5][3]["BESS.P"], name = "BESS", legendgroup = '5'),
              row=3, col=2)
################


fig.update_layout(
                  title_text="Microgrid Power Output from the openModelica Simulation")

fig.show()
filename = "scenario_subplot"
fig.write_image(filename + '.svg', engine = 'orca')
fig.write_image(filename + '.pdf', engine = 'orca')

Fontconfig warning: "/usr/share/fontconfig/conf.avail/05-reset-dirs-sample.conf", line 6: unknown element "reset-dirs"
[29976:0829/193016.226470:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[29976:0829/193022.855939:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command


In [51]:
#create title for plots
#create filename for plots
site_name = ["Scenario 1", "Scenario 2", "Scenario 3", "Scenario 4", "Scenario 5", "Scenario 6"]
plot_type = "Microgrid Output"
ei_title = {}
for i in range(len(df)):
        ei_title[i] = site_name[i] + "<br>" + plot_type + "<br>From: " +  df[i].time.min().strftime('%B %d, %Y') + " to " + df[i].time.max().strftime('%B %d, %Y')     
ei_title

{0: 'Scenario 1<br>Microgrid Output<br>From: March 01, 2022 to February 28, 2023',
 1: 'Scenario 2<br>Microgrid Output<br>From: March 01, 2022 to February 28, 2023',
 2: 'Scenario 3<br>Microgrid Output<br>From: March 01, 2022 to February 28, 2023',
 3: 'Scenario 4<br>Microgrid Output<br>From: March 01, 2022 to February 28, 2023',
 4: 'Scenario 5<br>Microgrid Output<br>From: March 01, 2022 to February 28, 2023',
 5: 'Scenario 6<br>Microgrid Output<br>From: March 01, 2022 to February 28, 2023'}

In [52]:
#create filename for plots
site_name = ["Scenario_1", "Scenario_2", "Scenario_3", "Scenario_4", "Scenario_5", "Scenario_6"]
plot_type = "Mg_Output"
ei_filename_list = {}
for i in range(len(df)):
        ei_filename_list[i] = str(i) + '_' + plot_type + '_' + df[i].time.min().strftime('%b_%d_%Y') + "_to_" + df[i].time.max().strftime('%b_%d_%Y') 
ei_filename_list

{0: '0_Mg_Output_Mar_01_2022_to_Feb_28_2023',
 1: '1_Mg_Output_Mar_01_2022_to_Feb_28_2023',
 2: '2_Mg_Output_Mar_01_2022_to_Feb_28_2023',
 3: '3_Mg_Output_Mar_01_2022_to_Feb_28_2023',
 4: '4_Mg_Output_Mar_01_2022_to_Feb_28_2023',
 5: '5_Mg_Output_Mar_01_2022_to_Feb_28_2023'}

In [53]:
x_title = "Time"
y_title = "Demand (kW)"
line_name = ["BESS", "Solar", "Grid Meter"]
line_color = ["deepskyblue", "red", "green"]
title = ei_title
filename = ei_filename_list
for i in range(len(df)):
    x_data = [df[i]['time']] * 3
    y_data = [df[i]["BESS.P"], df[i]["generator.P"], df[i]["grid.sou.S[1]"]]
    plot_graph(x_data, y_data, line_name, title[i], x_title, y_title, filename[i], line_color)

[18517:0812/170148.515186:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/170152.885440:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/170157.032358:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/170201.284982:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/170205.918205:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command
[18517:0812/170210.145124:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command


In [54]:
x_title = "Time"
y_title = "Demand (kW)"
line_name = ["Scenario 1", "Scenario 2", "Scenario 3", "Scenario 4", "Scenario 5", "Scenario 6"]
line_color = ["deepskyblue", "red", "green", "orange", 'aqua', 'yellow']
title = 'Scenario Comparison<br>Grid Meter<br>From: March 01, 2022 to February 28, 2023'
filename = 'net_load_scenario_comparison'
x_data = []
y_data = []
for i in range(len(df)):
    x_data.append(df[i]['time'])
    y_data.append(df[i]["grid.sou.S[1]"])
plot_graph(x_data, y_data, line_name, title, x_title, y_title, filename, line_color)

[18517:0812/170238.437802:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command


In [55]:
x_title = "Time"
y_title = "Demand (kW)"
line_name = ["Scenario 1", "Scenario 2", "Scenario 3", "Scenario 4", "Scenario 5", "Scenario 6"]
line_color = ["deepskyblue", "red", "green", "orange", 'aqua', 'yellow']
title = 'Scenario Comparison<br>Grid Meter<br>From: June 01, 2022 to July 01, 2022'
filename = 'net_load_scenario_comparison_summer'
x_data = []
y_data = []
for i in range(len(df)):
    x_data.append(df[i]['time'][df[i]['time'].between('06-01-2022', '07-01-2022')])
    y_data.append(df[i]["grid.sou.S[1]"][df[i]['time'].between('06-01-2022', '07-01-2022')])
plot_graph(x_data, y_data, line_name, title, x_title, y_title, filename, line_color)

[18517:0812/170252.490893:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command


In [56]:
x_title = "Time"
y_title = "Demand (kW)"
line_name = ["Level 2"]
line_color = ["deepskyblue"]
title = 'Level 2 Chargers<br>Power Output<br>From: March 01, 2022 to February 28, 2023'
filename = 'ev_l2_po'
x_data = [df[0]['time']]
y_data = [df[0]['ev_charger_level_2_load.P']]
plot_graph(x_data, y_data, line_name, title, x_title, y_title, filename, line_color)

[18517:0812/170305.899372:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command


In [57]:
x_title = "Time"
y_title = "Demand (kW)"
line_name = ["Level 3"]
line_color = ["deepskyblue"]
title = 'Level 3 Chargers<br>Power Output<br>From: March 01, 2022 to February 28, 2023'
filename = 'ev_l3_po'
x_data = [df[0]['time']]
y_data = [df[0]['ev_charger_level_3_load.P']]
plot_graph(x_data, y_data, line_name, title, x_title, y_title, filename, line_color)

[18517:0812/170313.447029:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command


In [58]:
x_title = "Time (Hours in a Day)"
y_title = "Emissions Rate (kg C02)"
line_name = ["Scenario 1", "Scenario 2", "Scenario 3", "Scenario 4", "Scenario 5", "Scenario 6"]
line_color = ["deepskyblue", "red", "green", "orange", 'aqua', 'yellow']
title = 'Scenario Comparison<br>Emissions Ouput<br>Average Day'
filename = 'emissions_scenario_comparison'
x_data = []
y_data = []
for i in range(len(df)):
    x_data.append(np.arange(24))
    y_data.append(edf[str(i)] * 1000)
plot_graph(x_data, y_data, line_name, title, x_title, y_title, filename, line_color)

[18517:0812/170318.307452:ERROR:buffer_manager.cc(488)] [.DisplayCompositor]GL ERROR :GL_INVALID_OPERATION : glBufferData: <- error from previous GL command


Scenarios